# NLP Word Embeddings


The groupwork of the group number two.

Source of truth: https://github.com/TurkuNLP/Deep_Learning_in_LangTech_course


##### The group

- Mikael Laine

- Naren "Puri" Purighalla

- Juho Kaasalainen

- Mari Salonen



## The task

Three tasks are to be done for the groupwork. The groupwork is divided into three milestones.

###### Milestone I

Train word2vec and vary the training parameters, especially the corpus, the window size, and the word2vec architecture (skip-gram vs. BoW). Inspect the embeddings manually using the nearest neighbor, and write up your observations. How do these models differ? For models trained on two different datasets, or with two different architectures, what is the proportion of nearest neighbors which remain unchanged? Can you see any more general trends here? Write a report on your findings. Choose any language you want for your tests.

###### Milestone II

There are many formal ways to evaluate the embeddings. Test all your models on several of these, and rank them. Do you see any general trends here? Add these findings to your report. Evaluation datasets:
http://wordvectors.org -- web based evaluation of English similarity
https://github.com/spyysalo/wvlib -- several English datasets and evaluation scripts
analogy_fin and analogy_en in the data directory of the course

###### Milestone III

The analogy task uses a simple vector arithmetics to solve problems of the type "king - man + woman = queen". You have seen some of my skepticism towards this in the class, and you tested the validity of this arithmetics for yourself in the classes and in milestone 2. You were also shown how to map the embeddings - on the example of mapping between two languages. The king-man-woman-queen style analogy is naturally also a mapping of a kind and therefore it should be learnable like any other mapping. In this milestone, you should therefore solve the word analogy as a learnable task, applying to it your knowledge from the cross-lingual mapping example. Are you able to get any better results, especially for Finnish where the basic analogy does not work that great? Do the learned weights which combine the three vectors to obtain the fourth correspond to the +1 -1 and +1 as in the simple arithmetics? Or are they entirely different? Are there any differeces in performance on the various sub-tasks of the analogy dataset? Summarize your findings.

## Milestone I: Training models with word2vec

### Model parameters

- corpus: IMDB and Reuters
- window size: 3, 5, 7, 9
- architecture: CBOW and skip-gram

**Worth considering:**

- different starting values for weights (-alpha in Mikolov w2v)
- different amount of iterations/epochs
- datasets of min 1M tokens
- other word embedding algorithms (glove, fasttext)

Models should be saved into the `models/` directory. Naming should be model-corpus-windowsize-arch, e.g. `model-imdb-5-skip`.

Example usage of Mikolov's word2vec for our case (you need to modify filepaths for it to work):

`./word2vec -train reuters_51cls.json.tokenized -output model-reuters-3-cbow -window 3 -cbow 1`

#### Default parameters

```
WORD VECTOR estimation toolkit v 0.1c

Options:
Parameters for training:
	-train <file>
		Use text data from <file> to train the model
	-output <file>
		Use <file> to save the resulting word vectors / word clusters
	-size <int>
		Set size of word vectors; default is 100
	-window <int>
		Set max skip length between words; default is 5
	-sample <float>
		Set threshold for occurrence of words. Those that appear with higher frequency in the training data
		will be randomly down-sampled; default is 1e-3, useful range is (0, 1e-5)
    -hs <int>
		Use Hierarchical Softmax; default is 0 (not used)
	-negative <int>
		Number of negative examples; default is 5, common values are 3 - 10 (0 = not used)
	-threads <int>
		Use <int> threads (default 12)
	-iter <int>
		Run more training iterations (default 5)
	-min-count <int>
		This will discard words that appear less than <int> times; default is 5
	-alpha <float>
		Set the starting learning rate; default is 0.025 for skip-gram and 0.05 for CBOW
	-classes <int>
		Output word classes rather than word vectors; default number of classes is 0 (vectors are written)
	-debug <int>
		Set the debug mode (default = 2 = more info during training)
	-binary <int>
		Save the resulting vectors in binary moded; default is 0 (off)
	-save-vocab <file>
		The vocabulary will be saved to <file>
	-read-vocab <file>
		The vocabulary will be read from <file>, not constructed from the training data
	-cbow <int>
		Use the continuous bag of words model; default is 1 (use 0 for skip-gram model)

Examples:
./word2vec -train data.txt -output vec.txt -size 200 -window 5 -sample 1e-4 -negative 5 -hs 0 -binary 0 -cbow 1 -iter 3
```

#### On training and evaluation

We should consider training the model with a tailored training subset and evaluation subset. This way we can get data on accuracy etc. which we can use and compare to our manual research of the models, i.e. see if accuracy is considerably lower on a model that differs from other models. This is different from milestone 2, where we evaluate our models on a more generic scale.

### Reading the models

In [13]:
from gensim.models import KeyedVectors
import numpy
import os
import matplotlib.pyplot as plt
import matplotlib.patheffects as path_effects

model=KeyedVectors.load_word2vec_format("models/model-imdb-3-cbow", binary=False, limit=100000)
print("Most similar words for 'locomotive':")
print(model.most_similar("movie",topn=10))
print()

cutoff=100000

numpy.savetxt("vectors_giga_in.txt",model.vectors[:cutoff,:]) # save vectors for a file

# run tsne locally, input is an embedding matrix, output is an embedding matrix with reduced dimensions
os.system("python3 bhtsne/bhtsne.py --input vectors_giga_in.txt --output vectors_giga_out.txt")

m2d=numpy.loadtxt("vectors_giga_out.txt") # read new vectors from a file

# plot
fig, ax = plt.subplots(figsize=(50, 50), dpi=250)
plt.scatter(m2d[:,0],m2d[:,1],marker=",",color="yellow")
words=[(k,w.index) for k,w in model.vocab.items()][:100000] # read words from the embedding model
words=[w for w,i in sorted(words, key=lambda x:x[1])] # sort based on the index to make sure the order is correct
print(words[:50])

for i,(v,w) in enumerate(zip(m2d,words)):
    if i%200!=0: # show only every 200th word
        continue
    txt=plt.text(v[0],v[1],w,size=30,ha="center",va="center",color="black")
    txt.set_path_effects([path_effects.Stroke(linewidth=1, foreground='white'),
                   path_effects.Normal()])
    

plt.show()

Most similar words for 'locomotive':
[('film', 0.9417807459831238), ('flick', 0.7148846387863159), ('show', 0.6578330993652344), ('picture', 0.625020444393158), ('programme', 0.6037653088569641), ('turkey', 0.5978808999061584), ('it', 0.5721004009246826), ('sequel', 0.5705005526542664), ('series', 0.5556154251098633), ('tripe', 0.5412472486495972)]

['</s>', 'the', 'and', 'of', 'to', 'is', 'in', 'it', 'that', 'this', 'was', 'as', 'The', 'with', 'movie', 'for', 'film', 'but', 'on', 'you', 'are', 'his', 'not', 'have', 'be', 'he', 'one', 'by', 'at', 'all', 'an', 'who', 'they', 'from', 'like', 'It', 'so', 'her', 'or', 'about', 'out', 'has', 'just', 'some', 'good', 'can', 'more', 'very', 'up', 'what']


## Milestone II: Evaluation

##### Get some evaluation datasets

##### Test our models on the datasets

##### Ranking of the models

##### Some general trends